In [32]:
import json


def normalize_run_name(run_name):
    return run_name.replace("/", "_")

def save_for_plot(dir_name, df, run_names, xlabel="Dataset", ylabel="Matched as dups probability", plot_name="plot name", custom_layout={}, ranges={}, x_column=None, default_metric=None):
    import os
    files = {}
    os.makedirs(f"data/plots/{dir_name}", exist_ok=True)
    data = {}
    for run_name in run_names:
        data[run_name] = {
            "x": df[x_column].tolist() if x_column else [run_name],
            "y": df[run_name].tolist(),
            "label": run_name,
        }
    file_name = f"default.json"
    files["default"] = {"file": f"{file_name}"}
    with open(f"data/plots/{dir_name}/{file_name}", "w") as f:
        json.dump({
            "data": data,
            "layout": {
                "title": {
                    "text": plot_name,
                },
                "xaxis": {
                    "title": {
                        "text": xlabel,
                    },
                },
                "yaxis": {
                    # "range": ranges.get(view, None),
                    "title": {
                        "text": ylabel,
                    },
                },
                **custom_layout,
            }
        }, f)
    with open(f"data/plots/{dir_name}/index.json", "w") as f:
        json.dump({
            "files": files,
            "settings": {
                "defaultMetric": default_metric,
                "slider": None,
                "autoSetXRange": False,
                "type": "bar"
            }
        }, f)
    return files



1         2         3       4-8      8-16     16-32
1B    0.994974  0.005008  0.000018       0.0       0.0       0.0
10B   0.951508  0.047331  0.001144  0.000017       0.0       0.0
100B  0.608873  0.302822  0.074548  0.013757       0.0       0.0
350B  0.174147   0.30712  0.268018  0.250649  0.000065       0.0
1T    0.006232   0.03247  0.083743  0.817636   0.05991  0.000008

In [28]:
summarized_df.reset_index()

index         1         2         3       4-8      8-16     16-32
0    1B  0.994974  0.005008  0.000018       0.0       0.0       0.0
1   10B  0.951508  0.047331  0.001144  0.000017       0.0       0.0
2  100B  0.608873  0.302822  0.074548  0.013757       0.0       0.0
3  350B  0.174147   0.30712  0.268018  0.250649  0.000065       0.0
4    1T  0.006232   0.03247  0.083743  0.817636   0.05991  0.000008

In [57]:
import pandas as pd


df = pd.read_csv("./data/duplicates-simulation.csv", index_col=0)


def summarize_ranges(df):
    df_summarized = pd.DataFrame(
        index=["1", "2", "3", "4-8", "8-16", "16-32"], columns=df.columns
    )
    df_summarized.loc["1"] = df.iloc[0]
    df_summarized.loc["2"] = df.iloc[1]
    df_summarized.loc["3"] = df.iloc[2]
    df_summarized.loc["4-8"] = df.iloc[3:9].sum()
    df_summarized.loc["8-16"] = df.iloc[9:17].sum()
    df_summarized.loc["16-32"] = df.iloc[17:].sum()
    return df_summarized


summarized_df = summarize_ranges(df).T
cols = summarized_df.columns
summarized_df.reset_index(inplace=True)
save_for_plot(
    "duplicates-simul",
    summarized_df,
    cols,
    x_column="index",
    plot_name="Sampling from 1000 identical buckets with 200B tokens each",
    ylabel="Dataset fraction",
    xlabel="Sample size",
    default_metric="default",
    custom_layout={
        "barmode": "stack",
        "legend": {
            "title": {
                "text": "# duplicates",
                "font": {
                    "size": 14,
                    "weight": "bold",
                }
            },
            "font": {
                "size": 14,
            },
            "bgcolor": 'rgba(255, 255, 255, 0.9)',
            # "borderwidth": 1,
            "orientation": "v",
            "xanchor": "left",
            "yanchor": "bottom",
            "x": 0.01,
            "y": 0,
        },
    },
)

{'default': {'file': 'default.json'}}

In [17]:
# Take the sumarized_df and pivotdf

KeyError: 'index'

In [5]:
import pandas as pd
import matplotlib.pyplot as plt

import plotly.graph_objects as go

df = pd.read_csv("./data/duplicates-simulation.csv", index_col=0)

def summarize_ranges(df):
    df_summarized = pd.DataFrame(index=['1', '2', '3', '4-8', '8-16', '16-32'], columns=df.columns)
    df_summarized.loc['1'] = df.iloc[0]
    df_summarized.loc['2'] = df.iloc[1]
    df_summarized.loc['3'] = df.iloc[2]
    df_summarized.loc['4-8'] = df.iloc[3:9].sum()
    df_summarized.loc['8-16'] = df.iloc[9:17].sum()
    df_summarized.loc['16-32'] = df.iloc[17:].sum()
    return df_summarized

summarized_df = summarize_ranges(df).T

# Create a stacked bar chart using Plotly
fig = go.Figure()
for col in summarized_df.columns:
    fig.add_trace(go.Bar(
        x=summarized_df.index,
        y=summarized_df[col],
        name=col
    ))

fig.update_layout(
    barmode='stack',
    title_text="Sampling from 100 identical buckets with 200B tokens each",
    xaxis_title="Sample size",
    yaxis_title="Dataset fraction",
    yaxis=dict(range=[0, 1.000001]),
    legend_title="# duplicates",
)

fig.show()


In [3]:
summarized_df.index

Index(['1B', '10B', '100B', '350B', '1T'], dtype='object')